In [1]:
import utils.yolo_fun as yolo_fun
import utils.img_fun as img_fun
import os
import pandas as pd
from tqdm import tqdm  
import rasterio
from rasterio.windows import Window
from rasterio.errors import RasterioIOError
import numpy as np
import shutil

#valid_tiles = [13, 14, 15, 22, 23, 24, 35, 44, 45, 51, 52, 53, 54, 61, 62, 63, 70, 71, 72, 73, 81, 82]  

orthomosiac_coords = os.path.join('coords', 'coords_pinguiton_dec.csv')
coords_dir_sin_normalizar = os.path.join('coords', 'labels_sin_normalizar')
coords_dir_normalized = os.path.join('coords', 'labels_normalized')
os.makedirs(coords_dir_sin_normalizar, exist_ok=True)
os.makedirs(coords_dir_normalized, exist_ok=True)

subrecortes_dir = os.path.join('cut_tiles')
os.makedirs(subrecortes_dir, exist_ok=True)
path_doctorado = 'G:\\.shortcut-targets-by-id\\1pYgV5EIk4-LapLNhlCwpQaDAzuqNffXG\\doctorado_albert\\pinguiton\\ortho_dic_5000'



In [2]:

# PARTE 0: ITERAMOS SOBRE LAS IMÁGENES PARA RECORTARLAS

contador = 0
for img in os.listdir(path_doctorado):
    contador += 1
    if contador > 10:
        break
        continue
    try:
        # PARTE 1: Cargar la imagen y recortarla en imágenes más pequeñas de aproximadamente 500x500 píxeles
        print(f"\n\nRecortando imagen {img}...")
        print('_________________________________________________________')

        img_name = img.split('.')[0]
        

        tiff_file = os.path.join(path_doctorado, img_name + '.tif')


        # Sacamos un diccionario con toda la información de la imagen
        img_info = img_fun.get_img_info(tiff_file)
        WIDTH = img_info["width"]
        HEIGHT = img_info["height"]
        TOP_LEFT = img_info["top_left"]
        BOTTOM_RIGHT = img_info["bottom_right"]
        min_x, max_y = img_info['top_left']
        max_x, min_y = img_info['bottom_right']

        img_fun.crop_tile_into_subrecortes(tiff_file, subrecortes_dir, img_name)


        # PARTE 2 (OPCIONAL): EXTRACCIÓN DE METADATOS PARA CADA SUBRECORTE INDIVIUAL
        df_orthomosaic = pd.read_csv(orthomosiac_coords, encoding='ISO-8859-1')
        print("Datos Originales: \n", df_orthomosaic.head())

        # Filtrar los puntos que están dentro del tile
        filtered_data = df_orthomosaic[
            (df_orthomosaic['x_center'] >= min_x) & (df_orthomosaic['x_center'] <= max_x) &
            (df_orthomosaic['y_center'] >= min_y) & (df_orthomosaic['y_center'] <= max_y)
        ]
        filtered_data.to_csv(os.path.join('coords', 'coords_per_tile' ,f'coords_{img_name}.csv'), index=False)
        print(f"Datos filtrados guardados en 'coords/coords_per_tile/coords_{img_name}.csv'.")

     
    except RasterioIOError as e:
        print(f"Error al cargar la imagen con rasterio: {e}")
        continue
    except FileNotFoundError as e:
        print(f"Error: {e}")
        continue

    



Recortando imagen imagen-15-8.tif...
_________________________________________________________
Metadata:
---------
driver: GTiff
dtype: uint8
nodata: None
width: 5000
height: 5000
count: 4
crs: EPSG:4326
transform: | 0.00, 0.00,-59.21|
| 0.00,-0.00,-62.31|
| 0.00, 0.00, 1.00|
blockxsize: 256
blockysize: 256
tiled: True
compress: lzw
interleave: pixel

Coordenadas de las esquinas de la imagen:
TOP LEFT: (-59.213980474998074, -62.307177528123795)
BOTTOM RIGHT: (-59.212102454998075, -62.3080516081238)
Subrecortes generados en cut_tiles
Datos Originales: 
    class   x_center   y_center  width  height  tile
0      0 -59.209849 -62.285565     30      30   NaN
1      0 -59.209849 -62.285563     30      30   NaN
2      0 -59.209847 -62.285564     30      30   NaN
3      0 -59.209846 -62.285565     30      30   NaN
4      0 -59.209847 -62.285567     30      30   NaN
Datos filtrados guardados en 'coords/coords_per_tile/coords_imagen-15-8.csv'.


Recortando imagen imagen-13-4.tif...
__________

In [7]:
# PARTE 3: ASIGNACIÓN DE LABELS EN TXT A CADA SUBRECORTE

yolo_fun.generar_txt_yolo(
    subrecorte_dir = subrecortes_dir, 
    csv_file = orthomosiac_coords, 
    coords_dir = coords_dir_sin_normalizar
)

Generando archivos .txt: 100%|██████████| 166/166 [00:01<00:00, 133.73it/s]

Archivos .txt generados en coords\labels_sin_normalizar


In [ ]:


# Iteramos para normalizar las coordenadas de cara archivo.txt
for file in os.listdir(coords_dir_sin_normalizar):
    df_sin_normalizar = pd.read_csv(os.path.join(coords_dir_sin_normalizar, file), sep=' ', header=None)
    name_subrecorte = os.path.splitext(file)[0]
    subrecorte_file = os.path.join('cut_tiles', f"{name_subrecorte}.tiff")

    print(f"Normalizando archivo {file}...")
    coords_file = os.path.join(coords_dir_sin_normalizar, file)
    output_file = os.path.join(coords_dir_normalized, file)
    
    yolo_fun.normalize_yolo_coords(
        tiff_file = subrecorte_file,
        coords_sin_normalizar = df_sin_normalizar, 
        output_file = output_file, 
    )


In [2]:


# PARTE 4: CLASIFICAR CONJUNTOS DE TRAIN Y VAL
for n_tile in range(14, 99):
    try:
        counter = 0
        subrecorte_dir = os.path.join('cut_tiles')
        for img in os.listdir(subrecorte_dir):
          
            img_name = os.path.splitext(img)[0]  # Divide entre el nombre del archivo y la extensión
            txt_path = os.path.join(coords_dir_normalized, f'{img_name}.txt')
            
            if os.path.getsize(txt_path) > 0:  # Solo copiar si el archivo .txt tiene contenido
                img_full_path = os.path.join(subrecorte_dir, img)
                txt_full_path = os.path.join(coords_dir_normalized, f'{img_name}.txt')

                # Alternar entre train y val con el contador
                if counter >= 9:
                    shutil.copy(img_full_path, os.path.join('datasets', 'penguin_dataset', 'images', 'val'))
                    shutil.copy(txt_full_path, os.path.join('datasets', 'penguin_dataset', 'labels', 'val'))
                    print(f"Imagen {img} y archivo {txt_path} copiados a 'datasets/penguin_dataset/images/val' y 'datasets/penguin_dataset/labels/val'.")
                else:
                    shutil.copy(img_full_path, os.path.join('datasets', 'penguin_dataset', 'images', 'train'))
                    shutil.copy(txt_full_path, os.path.join('datasets', 'penguin_dataset', 'labels', 'train'))
                    print(f"Imagen {img} y archivo {txt_path} copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.")
                
                counter = 0 if counter >= 10 else counter + 1
            
            else:
                print(f"Archivo {txt_path} vacío. No se copiará la imagen {img}.")
  
    except FileNotFoundError as e:
        print(f"Error: {e}")
        continue
    except Exception as e:
        print(f"Error: {e}")
        continue

Imagen tile_13_subrecorte_316.tiff y archivo coords\labels_normalized\tile_13_subrecorte_316.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_317.tiff y archivo coords\labels_normalized\tile_13_subrecorte_317.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_368.tiff y archivo coords\labels_normalized\tile_13_subrecorte_368.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_371.tiff y archivo coords\labels_normalized\tile_13_subrecorte_371.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_372.tiff y archivo coords\labels_normalized\tile_13_subrecorte_372.txt copiados a 'datasets/penguin_dataset/images/train' y 'datasets/penguin_dataset/labels/train'.
Imagen tile_13_subrecorte_379.tiff y archivo 